In [1]:
import pandas as pd
import numpy as np
import plotly.express as px
import warnings
from bslib import bslib as bsl
from hplib import hplib as hpl
import docs.heatstorage as hs
warnings.filterwarnings('ignore')

KWK-Profil

In [61]:
# generate a normalized (W/kW_el) chp 
# electrical production profile based on...
# - an on/off chp 
# - weather data for test reference region 4 (Potsdam)  
# - heating limit outside temperature = 15°C 
# - fraction of 10% for domestic hot water and 90% space heating

# Choose weather
TRJ = [4]
Years = [2015]
Types = ['a']
# Fixed parameters
t_room = 20         # Innenraumtemperatur in °C
P_tww = 1000        # Additional heating power for domestic hot water in W
E_th_tww = 2000     # heating consumption for domestic hot water in kWh/a
A = 150             # Living area of building
dt = 900            # timestep in s
T_hyst = 5          # hysteresis-temperature for thermal storages

# thermal storages
HeatStorage_h = hs.HeatStorage(
    Volume=500, ambient_temperature=20)  # heating
HeatStorage_tww = hs.HeatStorage(
    Volume=500, ambient_temperature=20)  # domestic hot water

# building class for standard single family house
# - Q_sp = specific heat demand in W/(m² K)
# - T_limit = heating limit outside temperature
# - T_vl_max = maximum flow temperature (hot) at reference outside temperature
# - T_rl_max = maximum flow temperature (cold) at reference outside temperature
# - f_hs_exp = dimensioning factor for heating system
buildings = pd.DataFrame([[1.2, 15, 55, 45, 1.1]],
                         columns=['Q_sp', 'T_limit', 'T_vl_max',
                                  'T_rl_max', 'f_hs_exp'],
                         index=['old'])

# initialize timestamp
dtime = pd.date_range('2015-01-01 00:00', '2015-12-31 23:45',
                      freq='15min', tz="Europe/Berlin")
dtime1 = pd.date_range('2015-01-01 00:00', '2015-12-31 23:59',
                      freq='1min', tz="Europe/Berlin")

# load locations
locations = pd.read_csv('../weather/data_processed/TRY.csv')

# Index
reihe = 0

# Weather
weather_1min = pd.read_csv('docs/weather_4_a_2015_1min.csv')
weather_1min.index = dtime1
weather = weather_1min.resample('15T').mean().round(1)

# Loads
loads_1min = pd.read_csv('docs/loads_4_a_2015_1min.csv')
loads_1min.index = dtime1
loads = loads_1min.resample('15T').mean().round(1)

for building in buildings.index:
    # Heizsystem initialisieren
    HS = hpl.HeatingSystem(t_outside_min=locations['T_min_ref'][3],
                            t_inside_set=t_room,
                            t_hs_set=[buildings['T_vl_max'][building],
                                        buildings['T_rl_max'][building]],
                            f_hs_exp=buildings['f_hs_exp'][building])

    # maximum heating power of building 
    P_th_max = (t_room - (locations['T_min_ref'][3])
                ) * buildings['Q_sp'][building] * A + P_tww
    P_th_ref = P_th_max

    # define CHP power
    P_CHP_tot = 0.75 * P_th_ref      # W
    # Thermal rated CHP power shall be around 50% of maximum heating power of building
    P_CHP_th_nom = P_CHP_tot * 0.65 # W
    P_CHP_el_nom = P_CHP_tot * 0.25 # W

    # Simulation loop
    # Initial values
    T_sp_h = buildings['T_vl_max'][building]
    T_sp_tww = 50  # Temperatur beim Start in °C
    P_chp_h = 0  # th. Leistung der KWK für Heizung beim Start in W
    P_chp_tww = 0  # th. Leistung der KWK für TWW beim Start in W
    hyst_h = 0  # Hysterese-Schalter Heizung
    hyst_tww = 0  # Hysterese-Schalter Trinkwarmwasser
    runtime = 0  # Laufzeit der KWK
    # Ergebnis DataFrame Zeitreihen
    results_timeseries = pd.DataFrame(index=dtime)

    # Timeseries Results
    T_SP_h = []
    T_SP_h_set = []
    T_SP_tww = []
    P_LOAD_h = []
    P_LOAD_tww = []
    P_CHP_h_th = []
    P_CHP_tww_th = []
    P_CHP_h_el = []
    P_CHP_tww_el = []
    P_GASHEATER_h = []
    P_GASHEATER_tww = []
    Runtime = []

    for t in weather.index:
        # Soll-Temperaturen
        T_sp_tww_set = 47
        T_vl = HS.calc_heating_dist_temp(
            weather.at[t, 'temperature 24h [degC]'])[0]
        T_rl = HS.calc_heating_dist_temp(
            weather.at[t, 'temperature 24h [degC]'])[1]
        T_sp_h_set = T_vl

        # Lasten
        P_load_tww_th = loads.at[t,
                                    'SFH-'+building+'_P_th_tww']
        P_load_h_th = loads.at[t,
                                'SFH-'+building+'_P_th_h_calc']

        # Trinkwarmwasser: Regelung
        if T_sp_tww < T_sp_tww_set and hyst_tww == 0:
            hyst_tww = 1
        if T_sp_tww < T_sp_tww_set+T_hyst and hyst_tww == 1:
            P_chp_tww_th = P_CHP_th_nom
            P_chp_tww_el = P_CHP_el_nom
            runtime = runtime+1/4
        else:
            hyst_tww = 0
            P_chp_tww_th = 0
            P_chp_tww_el = 0

        # Trinkwarmwasser: Speichertemperatur
        T_sp_tww = HeatStorage_tww.calculate_new_storage_temperature(T_sp=T_sp_tww,
                                                                        dt=dt,
                                                                        P_hp=P_chp_tww_th,
                                                                        P_ld=P_load_tww_th)
        if T_sp_tww < T_sp_tww_set-5:
            T_sp_tww = T_sp_tww + \
                (1/(HeatStorage_tww.V_sp*HeatStorage_tww.c_w)
                    ) * P_th_ref * dt
            P_GASHEATER_tww.append(P_th_ref)
        else:
            P_GASHEATER_tww.append(0)

        # Heizung: Regelung
        if T_sp_h < T_sp_h_set and hyst_h == 0 and hyst_tww == 0:
            hyst_h = 1

        if T_sp_h < T_sp_h_set+T_hyst and hyst_h == 1 and hyst_tww == 0:
            P_chp_h_th = P_CHP_th_nom
            P_chp_h_el = P_CHP_el_nom
            runtime = runtime+1/4

        else:
            hyst_h = 0
            P_chp_h_th = 0
            P_chp_h_el = 0

        # Heizung: Speichertemperaturen
        T_sp_h = HeatStorage_h.calculate_new_storage_temperature(T_sp=T_sp_h,
                                                                    dt=dt,
                                                                    P_hp=P_chp_h_th,
                                                                    P_ld=P_load_h_th)
        if T_sp_h < T_sp_h_set-5:
            T_sp_h = T_sp_h + \
                (1/(HeatStorage_h.V_sp*HeatStorage_h.c_w)) * \
                P_th_ref * dt
            P_GASHEATER_h.append(P_th_ref)
        else:
            P_GASHEATER_h.append(0)

        # Abspeichern relevanter Werte
        T_SP_h.append(T_sp_h)
        T_SP_h_set.append(T_sp_h_set)
        T_SP_tww.append(T_sp_tww)
        P_LOAD_h.append(P_load_h_th)
        P_LOAD_tww.append(P_load_tww_th)
        P_CHP_h_th.append(P_chp_h_th)
        P_CHP_tww_th.append(P_chp_tww_th)
        P_CHP_h_el.append(P_chp_h_el)
        P_CHP_tww_el.append(P_chp_tww_el)
        Runtime.append(runtime)

    results_timeseries['T_sp_h'] = T_SP_h
    results_timeseries['T_sp_h_set'] = T_SP_h_set
    results_timeseries['T_sp_tww'] = T_SP_tww
    results_timeseries['P_load_h'] = P_LOAD_h
    results_timeseries['P_load_tww'] = P_LOAD_tww
    results_timeseries['P_chp_h_th'] = P_CHP_h_th
    results_timeseries['P_chp_tww_th'] = P_CHP_tww_th
    results_timeseries['P_chp_h_el'] = P_CHP_h_el
    results_timeseries['P_chp_tww_el'] = P_CHP_tww_el
    results_timeseries['P_gasheater_h'] = P_GASHEATER_h
    results_timeseries['P_gasheater_tww'] = P_GASHEATER_tww
    results_timeseries['Runtime'] = Runtime

    # Abpeichern der Zeitreihe und Log
    results_timeseries.to_csv('docs/chp-onoff_4_a_2015_15min.csv')

# Sum up electrical production normalize to nominal electrical power
LP_CHP = pd.DataFrame()
LP_CHP.index = dtime
LP_CHP['on-off [W/kW_el]'] = results_timeseries['P_chp_h_el'] + results_timeseries['P_chp_tww_el']
LP_CHP['on-off [W/kW_el]'] = (LP_CHP['on-off [W/kW_el]']/(P_CHP_el_nom/1000))


In [62]:
px.line(results_timeseries['Runtime'])

In [63]:
# generate a normalized (W/kW_el) chp 
# electrical production profile based on...
# - an regulated chp 
# - weather data for test reference region 4 (Potsdam)  
# - heating limit outside temperature = 15°C 
# - fraction of 10% for domestic hot water and 90% space heating

# Choose weather
TRJ = [4]
Years = [2015]
Types = ['a']
# Fixed parameters
t_room = 20         # Innenraumtemperatur in °C
P_tww = 1000        # Additional heating power for domestic hot water in W
E_th_tww = 2000     # heating consumption for domestic hot water in kWh/a
A = 150             # Living area of building
dt = 900            # timestep in s
T_hyst = 5          # hysteresis-temperature for thermal storages

# thermal storages
HeatStorage_h = hs.HeatStorage(
    Volume=500, ambient_temperature=20)  # heating
HeatStorage_tww = hs.HeatStorage(
    Volume=500, ambient_temperature=20)  # domestic hot water

# building class for standard single family house
# - Q_sp = specific heat demand in W/(m² K)
# - T_limit = heating limit outside temperature
# - T_vl_max = maximum flow temperature (hot) at reference outside temperature
# - T_rl_max = maximum flow temperature (cold) at reference outside temperature
# - f_hs_exp = dimensioning factor for heating system
buildings = pd.DataFrame([[1.2, 15, 55, 45, 1.1]],
                         columns=['Q_sp', 'T_limit', 'T_vl_max',
                                  'T_rl_max', 'f_hs_exp'],
                         index=['old'])

# initialize timestamp
dtime = pd.date_range('2015-01-01 00:00', '2015-12-31 23:45',
                      freq='15min', tz="Europe/Berlin")
dtime1 = pd.date_range('2015-01-01 00:00', '2015-12-31 23:59',
                      freq='1min', tz="Europe/Berlin")

# load locations
locations = pd.read_csv('../weather/data_processed/TRY.csv')

# Index
reihe = 0

# Weather
weather_1min = pd.read_csv('docs/weather_4_a_2015_1min.csv')
weather_1min.index = dtime1
weather = weather_1min.resample('15T').mean().round(1)

# Loads
loads_1min = pd.read_csv('docs/loads_4_a_2015_1min.csv')
loads_1min.index = dtime1
loads = loads_1min.resample('15T').mean().round(1)

for building in buildings.index:
    # Heizsystem initialisieren
    HS = hpl.HeatingSystem(t_outside_min=locations['T_min_ref'][3],
                            t_inside_set=t_room,
                            t_hs_set=[buildings['T_vl_max'][building],
                                        buildings['T_rl_max'][building]],
                            f_hs_exp=buildings['f_hs_exp'][building])

    # maximum heating power of building 
    P_th_max = (t_room - (locations['T_min_ref'][3])
                ) * buildings['Q_sp'][building] * A + P_tww
    P_th_ref = P_th_max

    # define CHP power
    P_CHP_tot = 0.75 * P_th_ref      # W
    # Thermal rated CHP power shall be around 33% of maximum heating power of building
    P_CHP_th_nom = P_CHP_tot * 0.65 # W
    P_CHP_el_nom = P_CHP_tot * 0.25 # W

    # Simulation loop
    # Initial values
    T_sp_h = buildings['T_vl_max'][building]
    T_sp_tww = 50  # Temperatur beim Start in °C
    P_chp_h = 0  # th. Leistung der KWK für Heizung beim Start in W
    P_chp_tww = 0  # th. Leistung der KWK für TWW beim Start in W
    hyst_h = 0  # Hysterese-Schalter Heizung
    hyst_tww = 0  # Hysterese-Schalter Trinkwarmwasser
    runtime = 0  # Laufzeit der KWK
    # Ergebnis DataFrame Zeitreihen
    results_timeseries = pd.DataFrame(index=dtime)

    # Timeseries Results
    T_SP_h = []
    T_SP_h_set = []
    T_SP_tww = []
    P_LOAD_h = []
    P_LOAD_tww = []
    P_CHP_h_th = []
    P_CHP_tww_th = []
    P_CHP_h_el = []
    P_CHP_tww_el = []
    P_GASHEATER_h = []
    P_GASHEATER_tww = []
    Runtime = []

    for t in weather.index:
        # Soll-Temperaturen
        T_sp_tww_set = 47
        T_vl = HS.calc_heating_dist_temp(
            weather.at[t, 'temperature 24h [degC]'])[0]
        T_rl = HS.calc_heating_dist_temp(
            weather.at[t, 'temperature 24h [degC]'])[1]
        T_sp_h_set = T_vl
        
        # Lasten
        P_load_tww_th = loads.at[t,
                                    'SFH-'+building+'_P_th_tww']
        P_load_h_th = loads.at[t,
                                'SFH-'+building+'_P_th_h_calc']

        # Trinkwarmwasser: Regelung
        if T_sp_tww < T_sp_tww_set and hyst_tww == 0:
            hyst_tww = 1
        if T_sp_tww < T_sp_tww_set+T_hyst and hyst_tww == 1:
            P_chp_tww_th = P_CHP_th_nom
            P_chp_tww_el = P_CHP_el_nom
            runtime = runtime+1/4
        else:
            hyst_tww = 0
            P_chp_tww_th = 0
            P_chp_tww_el = 0

        # Trinkwarmwasser: Speichertemperatur
        T_sp_tww = HeatStorage_tww.calculate_new_storage_temperature(T_sp=T_sp_tww,
                                                                        dt=dt,
                                                                        P_hp=P_chp_tww_th,
                                                                        P_ld=P_load_tww_th)
        if T_sp_tww < T_sp_tww_set-5:
            T_sp_tww = T_sp_tww + \
                (1/(HeatStorage_tww.V_sp*HeatStorage_tww.c_w)
                    ) * P_th_ref * dt
            P_GASHEATER_tww.append(P_th_ref)
        else:
            P_GASHEATER_tww.append(0)

        # Heizung: Regelung
        if T_sp_h < T_sp_h_set and hyst_h == 0 and hyst_tww == 0:
            hyst_h = 1

        if T_sp_h < T_sp_h_set+T_hyst and hyst_h == 1 and hyst_tww == 0:
            if P_load_h_th > P_CHP_th_nom:
                P_chp_h_th = P_CHP_th_nom
                P_chp_h_el = P_CHP_el_nom
                runtime = runtime+1/4
            else:
                P_chp_h_th = max(P_load_h_th,0.2*P_CHP_th_nom)
                P_chp_h_el = max(P_load_h_th,0.2*P_CHP_th_nom) * (0.25 / 0.65)
                runtime = runtime+1/4

        else:
            hyst_h = 0
            P_chp_h_th = 0
            P_chp_h_el = 0

        # Heizung: Speichertemperaturen
        T_sp_h = HeatStorage_h.calculate_new_storage_temperature(T_sp=T_sp_h,
                                                                    dt=dt,
                                                                    P_hp=P_chp_h_th,
                                                                    P_ld=P_load_h_th)
        if T_sp_h < T_sp_h_set-5:
            T_sp_h = T_sp_h + \
                (1/(HeatStorage_h.V_sp*HeatStorage_h.c_w)) * \
                P_th_ref * dt
            P_GASHEATER_h.append(P_th_ref)
        else:
            P_GASHEATER_h.append(0)

        # Abspeichern relevanter Werte
        T_SP_h.append(T_sp_h)
        T_SP_h_set.append(T_sp_h_set)
        T_SP_tww.append(T_sp_tww)
        P_LOAD_h.append(P_load_h_th)
        P_LOAD_tww.append(P_load_tww_th)
        P_CHP_h_th.append(P_chp_h_th)
        P_CHP_tww_th.append(P_chp_tww_th)
        P_CHP_h_el.append(P_chp_h_el)
        P_CHP_tww_el.append(P_chp_tww_el)
        Runtime.append(runtime)

    results_timeseries['T_sp_h'] = T_SP_h
    results_timeseries['T_sp_h_set'] = T_SP_h_set
    results_timeseries['T_sp_tww'] = T_SP_tww
    results_timeseries['P_load_h'] = P_LOAD_h
    results_timeseries['P_load_tww'] = P_LOAD_tww
    results_timeseries['P_chp_h_th'] = P_CHP_h_th
    results_timeseries['P_chp_tww_th'] = P_CHP_tww_th
    results_timeseries['P_chp_h_el'] = P_CHP_h_el
    results_timeseries['P_chp_tww_el'] = P_CHP_tww_el
    results_timeseries['P_gasheater_h'] = P_GASHEATER_h
    results_timeseries['P_gasheater_tww'] = P_GASHEATER_tww
    results_timeseries['Runtime'] = Runtime

    # Abpeichern der Zeitreihe und Log
    results_timeseries.to_csv('docs/chp-regulated_4_a_2015_15min.csv')

# Sum up electrical production normalize to nominal electrical power
LP_CHP['regulated [W/kW_el]'] = results_timeseries['P_chp_h_el'] + results_timeseries['P_chp_tww_el']
LP_CHP['regulated [W/kW_el]'] = (LP_CHP['regulated [W/kW_el]']/(P_CHP_el_nom/1000))


In [64]:
px.line(results_timeseries['Runtime'])

In [67]:
LP_CHP.round(1).to_csv('data_processed/15min/chp_4_a_2015_15min.csv', index_label='datetime')
px.line(LP_CHP)